In [2]:
pip show transformers

Name: transformers
Version: 4.35.2
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /usr/local/lib/python3.10/dist-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
Required-by: 


## Importation des données

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
%cd "/content/drive/MyDrive/M2 DATASCALE/Fouilles de données/GPT_fintuning_test/data"

/content/drive/MyDrive/M2 DATASCALE/Fouilles de données/GPT_fintuning_test/data


In [5]:
!ls

alldata_1_for_kaggle.csv  chatbot_model  ori_data.json	ori_pqaa.json  ori_pqau.json


In [6]:
import pandas as pd
import json

In [7]:
with open('ori_pqau.json') as f:
    data1 = json.load(f)
# Conversion en DataFrame
df1 = pd.DataFrame(data1.values(), index=data1.keys())
df1 = df1[['QUESTION', 'LONG_ANSWER']]
df1.columns = ['QUESTION','ANSWER']
df1


QUESTION  \
14499029  Is naturopathy as effective as conventional th...   
14499049  Can randomised trials rely on existing electro...   
14499672  Is laparoscopic radical prostatectomy better t...   
14499773  Does bacterial gastroenteritis predispose peop...   
14499777  Is early colonoscopy after admission for acute...   
...                                                     ...   
10632750  Diversion colitis in children: an iatrogenic a...   
10632796  Raising research awareness among midwives and ...   
10632828  Delivery of primary care to women. Do women's ...   
10633786  Analysis of failures after whole abdominal irr...   
10634050  Loco-regional block in ophthalmic surgery: sin...   

                                                     ANSWER  
14499029  Naturopathy appears to be an effective alterna...  
14499049  Routine data have the potential to support hea...  
14499672  The results of our non-randomized study show t...  
14499773  Symptoms consistent with IBS and functional di...  
14499777  No significant association is apparent between...  
...                                                     ...  
10632750  Histological features of DC in children are ve...  
10632796  The introduction of clinical governance challe...  
10632828  These results suggest that, at least in this s...  
10633786  General prophylactic enclosure of the inguinal...  
10634050  Local anaesthetics mixture with hyaluronidase ...  

[61249 rows x 2 columns]

In [8]:
with open('ori_pqaa.json') as f:
  data2=json.load(f)
  # Conversion en DataFrame
df2 = pd.DataFrame(data2.values(), index=data2.keys())
df2 = df2[['QUESTION', 'LONG_ANSWER']]
df2.columns = ['QUESTION','ANSWER']
df2

QUESTION  \
25429730  Are group 2 innate lymphoid cells ( ILC2s ) in...   
25433161  Does vagus nerve contribute to the development...   
25445714  Does psammaplin A induce Sirtuin 1-dependent a...   
25431941  Is methylation of the FGFR2 gene associated wi...   
25432519  Do tumor-infiltrating immune cell profiles and...   
...                                                     ...   
8217974   Is urine production rate related to behavioura...   
8204319   Does evaluation of the use of general practice...   
8205673   Does intracoronary angiotensin-converting enzy...   
8215873   Does transfusion significantly increase the ri...   
8201088   Is low intramucosal pH associated with failure...   

                                                     ANSWER  
25429730  As ILC2s are elevated in patients with CRSwNP,...  
25433161  Neuronal signals via the hepatic vagus nerve c...  
25445714  PsA significantly inhibited MCF-7/adr cells pr...  
25431941  We identified a novel biologically plausible c...  
25432519  Breast cancer immune cell subpopulation profil...  
...                                                     ...  
8217974   During active sleep (state 2F) hourly fetal ur...  
8204319   General practice registers can provide a suita...  
8205673   Intracoronary enalaprilat resulted in an impro...  
8215873   The choice between splenectomy and splenic rep...  
8201088   Some critically ill patients with low gastric ...  

[211269 rows x 2 columns]

In [9]:
# union des deux df
df_union = pd.concat([df1, df2], ignore_index=True)
df_union


QUESTION  \
0       Is naturopathy as effective as conventional th...   
1       Can randomised trials rely on existing electro...   
2       Is laparoscopic radical prostatectomy better t...   
3       Does bacterial gastroenteritis predispose peop...   
4       Is early colonoscopy after admission for acute...   
...                                                   ...   
272513  Is urine production rate related to behavioura...   
272514  Does evaluation of the use of general practice...   
272515  Does intracoronary angiotensin-converting enzy...   
272516  Does transfusion significantly increase the ri...   
272517  Is low intramucosal pH associated with failure...   

                                                   ANSWER  
0       Naturopathy appears to be an effective alterna...  
1       Routine data have the potential to support hea...  
2       The results of our non-randomized study show t...  
3       Symptoms consistent with IBS and functional di...  
4       No significant association is apparent between...  
...                                                   ...  
272513  During active sleep (state 2F) hourly fetal ur...  
272514  General practice registers can provide a suita...  
272515  Intracoronary enalaprilat resulted in an impro...  
272516  The choice between splenectomy and splenic rep...  
272517  Some critically ill patients with low gastric ...  

[272518 rows x 2 columns]

In [25]:
ori_data_json= df_union.to_json(orient='records')


In [26]:
!ls

alldata_1_for_kaggle.csv  chatbot_model  ori_data.json	ori_pqaa.json  ori_pqau.json


In [27]:
with open("./ori_data.json", 'w') as fichier_json:
    fichier_json.write(ori_data_json)

In [28]:
from transformers import GPT2Tokenizer, GPT2LMHeadModel, AdamW

In [14]:
model = GPT2LMHeadModel.from_pretrained('gpt2')
tokenizer = GPT2Tokenizer.from_pretrained('gpt2')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [15]:
# Test the tokenizer
text = "I play football."
tokens1 = tokenizer(text)
tokens2 = tokenizer.encode(text)
tokens3 = tokenizer.batch_encode_plus([text])
print(f"Tokens 1: {tokens1}\n")
print(f"Tokens 2: {tokens2}\n")
print(f"Tokens 3: {tokens3}\n")
print(f"The token of id: {tokens1['input_ids'][0]} is {tokenizer.decode(tokens1['input_ids'][0])}")

Tokens 1: {'input_ids': [40, 711, 4346, 13], 'attention_mask': [1, 1, 1, 1]}

Tokens 2: [40, 711, 4346, 13]

Tokens 3: {'input_ids': [[40, 711, 4346, 13]], 'attention_mask': [[1, 1, 1, 1]]}

The token of id: 40 is I


In [16]:
import torch
from torch.utils.data import Dataset, DataLoader
from transformers import GPT2LMHeadModel, GPT2Tokenizer
from transformers import get_linear_schedule_with_warmup
from torch.optim import AdamW

In [17]:
# Load pre-trained GPT-2 tokenizer and model
tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
tokenizer.pad_token = tokenizer.eos_token
model = GPT2LMHeadModel.from_pretrained('gpt2')

## concernant data_json

In [29]:
data_json = json.loads(ori_data_json)
data_json = data_json[:5000]

In [30]:
print(data_json)

[{'QUESTION': 'Is naturopathy as effective as conventional therapy for treatment of menopausal symptoms?', 'ANSWER': 'Naturopathy appears to be an effective alternative for relief of specific menopausal symptoms compared to conventional therapy.'}, {'QUESTION': 'Can randomised trials rely on existing electronic data?', 'ANSWER': 'Routine data have the potential to support health technology assessment by RCTs. The cost of data collection and analysis is likely to fall, although further work is required to improve the validity of routine data, particularly in central returns. Better knowledge of the capability of local systems and access to the data held on them is also essential. Routinely captured clinical data have real potential to measure patient outcomes, particularly if the detail and precision of the data could be improved.'}, {'QUESTION': 'Is laparoscopic radical prostatectomy better than traditional retropubic radical prostatectomy?', 'ANSWER': 'The results of our non-randomize

In [31]:
# Initialiser des listes vides pour stocker les questions et les réponses
questions = []
answers = []

# Parcourir le JSON et extraire les questions et réponses
for item in data_json:
    questions.append(item["QUESTION"])
    answers.append(item["ANSWER"])


In [34]:
# Initialiser une liste vide pour stocker les paires question-réponse
question_answer_pairs = []

# Parcourir le JSON et extraire les paires question-réponse
for item in data_json:
    question = item["QUESTION"]
    answer = item["ANSWER"]
    concatenated_pair = f"{question} {answer}"
    question_answer_pairs.append(concatenated_pair)
print(question_answer_pairs)

['Is naturopathy as effective as conventional therapy for treatment of menopausal symptoms? Naturopathy appears to be an effective alternative for relief of specific menopausal symptoms compared to conventional therapy.', 'Can randomised trials rely on existing electronic data? Routine data have the potential to support health technology assessment by RCTs. The cost of data collection and analysis is likely to fall, although further work is required to improve the validity of routine data, particularly in central returns. Better knowledge of the capability of local systems and access to the data held on them is also essential. Routinely captured clinical data have real potential to measure patient outcomes, particularly if the detail and precision of the data could be improved.', 'Is laparoscopic radical prostatectomy better than traditional retropubic radical prostatectomy? The results of our non-randomized study show that up to now laparoscopic radical prostatectomy does not provide 

In [32]:
print("Questions (100 premières):", questions)
print("Answers (100 premières):", answers)

Questions (100 premières): ['Is naturopathy as effective as conventional therapy for treatment of menopausal symptoms?', 'Can randomised trials rely on existing electronic data?', 'Is laparoscopic radical prostatectomy better than traditional retropubic radical prostatectomy?', 'Does bacterial gastroenteritis predispose people to functional gastrointestinal disorders?', 'Is early colonoscopy after admission for acute diverticular bleeding needed?', 'Does the use of a specialised paediatric retrieval service result in the loss of vital stabilisation skills among referring hospital staff?', 'Management of thoracic empyema in childhood: does the pleural thickening matter?', 'Does repeated hyperbaric exposure to 4 atmosphere absolute cause hearing impairment?', 'Lower urinary tract reconstruction for duplicated renal units with ureterocele. Is excision of the ureterocele with reconstruction of the bladder base necessary?', 'Is common sheath extravesical reimplantation an effective techniqu

In [35]:
tokenized_data = tokenizer.batch_encode_plus(
    question_answer_pairs,
    return_tensors='pt',
    padding='max_length',
    max_length=512
)

# Obtenir les tenseurs d'entrée et de sortie tokenisés
tokenized_inputs = tokenized_data["input_ids"]

In [36]:
tokenized_inputs

tensor([[ 3792, 34664,  1434,  ..., 50256, 50256, 50256],
        [ 6090,  4738,  1417,  ..., 50256, 50256, 50256],
        [ 3792, 14779,   283,  ..., 50256, 50256, 50256],
        ...,
        [13921, 17770,  9014,  ..., 50256, 50256, 50256],
        [ 6090, 26711,    12,  ..., 50256, 50256, 50256],
        [13921,  2546,  2300,  ..., 50256, 50256, 50256]])

In [21]:
# Tokenize and pad the dataset using batch_encode_plus
tokenized_inputs = tokenizer.batch_encode_plus(questions, return_tensors='pt', padding='max_length', max_length=200, truncation=True)["input_ids"]
tokenized_labels = tokenizer.batch_encode_plus(answers, return_tensors='pt', padding='max_length', max_length=200, truncation=True)["input_ids"]

In [22]:
class CustomDataset(Dataset):
  def __init__(self,input_ids,labels):
    self.input_ids= input_ids
    self.labels= labels

  def __len__(self):
    return len(self.input_ids)

  def __getitem__(self,idx):
    return self.input_ids[idx], self.labels[idx]



In [23]:
dataset = CustomDataset(tokenized_inputs, tokenized_labels)
dataloader = DataLoader(dataset, batch_size=2, shuffle=True)

In [ ]:
# Training parameters
epochs = 1
learning_rate = 5e-5

# Optimizer and scheduler
optimizer = AdamW(model.parameters(), lr=learning_rate)
total_steps = len(dataloader) * epochs
# Adjust learning rate during training for example
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=0, num_training_steps=total_steps)

# Training loop
for epoch in range(epochs):
    for batch in dataloader:
        optimizer.zero_grad()
        input_ids, labels = batch

        outputs = model(input_ids, labels=labels)
        loss = outputs.loss
        loss.backward()
        optimizer.step()
        scheduler.step()

# Save the fine-tuned model
model.save_pretrained("chatbot_model")
tokenizer.save_pretrained("chatbot_model")


/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [ ]:
# Load the trained chatbot
from transformers import GPT2LMHeadModel, GPT2Tokenizer

# Replace 'path/to/your/model' with the actual path where you saved your fine-tuned model
model_path = 'chatbot_model'
# Load the fine-tuned GPT-2 model
model = GPT2LMHeadModel.from_pretrained(model_path)
# Load the tokenizer associated with the model
tokenizer = GPT2Tokenizer.from_pretrained(model_path)

In [ ]:
# Input prompt for generation
prompt = "Is naturopathy as effective as conventional therapy for treatment of menopausal symptoms?"

# Tokenize the prompt
input_ids = tokenizer.encode(prompt, return_tensors="pt")

# Generate text
output = model.generate(input_ids, max_length=200, num_return_sequences=1, no_repeat_ngram_size=2, top_k=50, top_p=0.95, pad_token_id=tokenizer.pad_token_id, eos_token_id=tokenizer.eos_token_id, do_sample=True)

# Decode and print the generated text
generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
generated_text